# Environment Setup and Imports

In [1]:
# MoviePy Setup
!apt-get update
!apt-get install imagemagick -y
!pip install wand
!pip install gizeh
# TTS libraries
!pip install gTTS elevenlabs

!sed -i '/<policy domain="path" rights="none" pattern="@\*"/d' /etc/ImageMagick-6/policy.xml

Hit:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Get:7 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease [18.1 kB]
Hit:8 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:11 https://r2u.stat.illinois.edu/ubuntu jammy/main amd64 Packages [2,690 kB]
Get:12 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [2,788 kB]
Get:13 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 Packages

In [2]:
from collections import defaultdict
from PIL import Image, ImageDraw
import requests
import random
import string
import os

import numpy as np
import spacy
import torch
from transformers import Owlv2Processor, Owlv2ForObjectDetection
from transformers import BlipProcessor, BlipForConditionalGeneration

from gtts import gTTS
from elevenlabs.client import ElevenLabs, VoiceSettings

import gizeh
import cv2
from moviepy.editor import TextClip, ImageClip, VideoClip, AudioClip, AudioFileClip, CompositeVideoClip, concatenate_videoclips, concatenate_audioclips, concatenate
from scipy.ndimage import gaussian_filter

  if event.key is 'enter':



# Utility Functions

In [3]:
def get_image_by_url(image_url):
    return Image.open(requests.get(image_url, stream=True).raw)

def get_image_by_path(image_path):
    return Image.open(image_path)

def get_image(image_location, max_dim=720):
    """
    Download and preprocess an image from a URL.

    Args:
        image_location (str): URL of the image to download, or path to local image
        max_dim (int): Maximum dimension for resizing the image while maintaining aspect ratio

    Returns:
        np.ndarray: Processed image as a numpy array
    """
    if image_location.startswith("http"):
        image = get_image_by_url(image_location)
    else:
        image = get_image_by_path(image_location)

    if max(image.size) > max_dim:
        if image.size[0] > image.size[1]:
            image = image.resize((max_dim, int(max_dim * image.size[1] / image.size[0])))
        else:
            image = image.resize((int(max_dim * image.size[0] / image.size[1]), max_dim))

    # Guanrantee even dimensions for moviepy mp4 encoding compatibility
    if image.width % 2 != 0:
        image = image.crop((0, 0, image.width - 1, image.height))
    if image.height % 2 != 0:
        image = image.crop((0, 0, image.width, image.height - 1))
    return image

In [4]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

blip_processor = BlipProcessor.from_pretrained("Salesforce/blip-image-captioning-large")
blip_model = BlipForConditionalGeneration.from_pretrained("Salesforce/blip-image-captioning-large").to(device)

def get_image_caption(image):
    """
    Generate a caption for the input image using the pre-trained BLIP model.

    Args:
        image (np.ndarray): Input image to caption

    Returns:
        str: Generated caption for the image
    """
    inputs = blip_processor(image, return_tensors="pt").to(device)
    out = blip_model.generate(**inputs)
    return blip_processor.decode(out[0], skip_special_tokens=True)

Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(



preprocessor_config.json:   0%|          | 0.00/445 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/527 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/4.60k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.88G [00:00<?, ?B/s]

In [5]:
nlp = spacy.load("en_core_web_sm")

### Need work to combine some nouns connected by "a", "of" etc.
def get_nouns(text):
    """
    Extract nouns from a given text using NLP capabilities of Spacy.

    Args:
        text (str): Input text to analyze

    Returns:
        Tuple[List[str], List[str], List[str]]:
            - List[str]: List of extracted nouns
            - List[str]: List of corresponding subtitles
            - List[str]: List of parts of speech for each word
    """
    text = text.capitalize()
    doc = nlp(text)
    running_text = ""
    subtitles = []
    nouns = []
    prev = None
    for token in doc:
        if running_text:
            running_text += " " + token.text
        else:
            running_text = token.text
        if token.pos_ == "NOUN":
            if prev == "NOUN":
                nouns[-1] += " " + token.text
                subtitles[-1] = running_text
            else:
                nouns.append(token.text)
                subtitles.append(running_text)
        prev = token.pos_

    if not nouns:
        subtitles = [running_text]

    if subtitles[-1] != running_text:
        subtitles.append(running_text)

    parts_of_speech = [subtitles[0]]
    for i in range(1, len(subtitles)):
        parts_of_speech.append(subtitles[i][len(subtitles[i-1]) + 1:])

    return nouns, subtitles, parts_of_speech

In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

owl_processor = Owlv2Processor.from_pretrained("google/owlv2-base-patch16-ensemble")
owl_model = Owlv2ForObjectDetection.from_pretrained("google/owlv2-base-patch16-ensemble").to(device)

def get_nouns_bboxes(image, nouns, single_bbox=True, single_bbox_criteria="score", conf_thr=0.1):
    """
    Detect bounding boxes for nouns in the image using the OWL V2 pre-trained model.

    Args:
        image (np.ndarray): Input image
        nouns (List[str]): List of nouns to detect
        single_bbox (bool): Whether to return a single best bounding box per noun
        single_bbox_criteria (str): Criteria for selecting the best bounding box
        conf_thr (float): Confidence threshold for detection

    Returns:
        Dict[str, List[Tuple[float, float, float, float]]]: Dictionary mapping nouns to their bounding boxes
    """
    if single_bbox_criteria not in ["score", "area"]:
        raise ValueError(f"Unknown single_bbox_criteria: {single_bbox_criteria}")

    inputs = owl_processor(text=[nouns], images=image, return_tensors="pt").to(device)
    with torch.no_grad():
      outputs = owl_model(**inputs)
    target_sizes = torch.Tensor([image.size[::-1]])
    results = owl_processor.post_process_grounded_object_detection(outputs=outputs, threshold=conf_thr, target_sizes=target_sizes)
    boxes, scores, labels = results[0]["boxes"], results[0]["scores"], results[0]["labels"]

    bboxes_per_noun = defaultdict(list)
    for box, score, label in zip(boxes, scores, labels):
        box = [int(i) for i in box.tolist()]
        bboxes_per_noun[nouns[label]].append((box, score))

    for noun, bboxes_scores in bboxes_per_noun.items():
        if not single_bbox:
            bboxes_per_noun[noun] = [bbox for bbox, score in bboxes_scores]
        if single_bbox:
            if single_bbox_criteria == "score":
                bboxes_per_noun[noun] = max(bboxes_scores, key=lambda x: x[1])[0]
            if single_bbox_criteria == "area":
                bboxes_per_noun[noun] = max(bboxes_scores, key=lambda x: (x[0][2] - x[0][0]) * (x[0][3] - x[0][1]))[0]

    return bboxes_per_noun

preprocessor_config.json:   0%|          | 0.00/425 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.10k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.06M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/67.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/121 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/620M [00:00<?, ?B/s]

In [7]:
def filter_and_refine(nouns, subtitles, parts_of_speech, bboxes_per_noun):
    """
    Filter and refine the extracted nouns, subtitles, and bounding boxes.

    Args:
        nouns (List[str]): List of extracted nouns
        subtitles (List[str]): List of subtitles
        parts_of_speech (List[str]): List of parts of speech
        bboxes_per_noun (Dict[str, List[Tuple[float, float, float, float]]]): Bounding boxes per noun

    Returns:
        Tuple containing filtered and refined:
        - nouns
        - subtitles
        - parts_of_speech
    """
    if not nouns:
        return nouns, subtitles, parts_of_speech

    filtered_nouns = []
    filtered_subtitles = []
    filtered_parts_of_speech = []
    running_part_of_speech = ""

    for i, noun in enumerate(nouns):
        if noun not in bboxes_per_noun:
            if not running_part_of_speech:
                running_part_of_speech = parts_of_speech[i]
            else:
                running_part_of_speech += " " + parts_of_speech[i]
            continue
        filtered_nouns.append(noun)
        filtered_subtitles.append(subtitles[i])
        if running_part_of_speech:
            filtered_parts_of_speech.append(running_part_of_speech + " " + parts_of_speech[i])
        else:
            filtered_parts_of_speech.append(parts_of_speech[i])
        running_part_of_speech = ""

    return filtered_nouns, filtered_subtitles, filtered_parts_of_speech

In [8]:
def get_speech_from_text(parts_of_speech, time_per_noun, tts_library="gtts",
                         elevenlabs_api_key=None, temp_dir="temp"):
    """
    Generate speech from text and calculate speech lengths.

    Args:
        parts_of_speech (List[str]): List of parts of speech
        time_per_noun (float): Time allocated per noun
        tts_library (str): TTS library to use to generate speech ('gtts' or 'elevenlabs')
        elevenlabs_api_key (str): ElevenLabs API key if using elevenlabs TTS
        temp_dir (str): Directory for temporary files

    Returns:
        Tuple[AudioClip, List[float]]:
            - AudioClip: MoviePy AudioClip object containing the concatenated speech
            - List[float]: List of durations for each speech segment
    """
    if tts_library not in ["gtts", "elevenlabs"]:
        raise ValueError(f"Specified TTS library '{tts_library}' is not supported. Should be either 'gtts' or 'elevenlabs'.")
    if tts_library == "elevenlabs" and elevenlabs_api_key is None:
        raise ValueError("elevenlabs_api_key is required when using elevenlabs TTS library.")

    if tts_library == "elevenlabs":
        elevenlabs_client = ElevenLabs(api_key=ELEVENLABS_API_KEY)

    radom_prefix = ''.join(random.choices(string.ascii_uppercase + string.digits, k=10)) # to avoid overwriting existing files
    speechs = []
    speechs_len = []

    for i, part_of_speech in enumerate(parts_of_speech):
        if tts_library == "gtts":
            speech = gTTS(text=part_of_speech, lang='en', tld='co.uk', slow=False)
            speech.save(f"{temp_dir}/{radom_prefix}-{i}.mp3")
        else:
            speech = elevenlabs_client.text_to_speech.convert(
                text=part_of_speech,
                voice_id="XrExE9yKIg1WjnnlVkGX",
                model_id="eleven_multilingual_v2",
                output_format="mp3_44100_128",
                voice_settings=VoiceSettings(speed=0.9)
            )
            with open(f"{temp_dir}/{radom_prefix}-{i}.mp3", "wb") as file:
                for chunk in speech:  # Iterate through the generator to get audio chunks
                    file.write(chunk)  # Write each chunk to the file

        audio_clip = AudioFileClip(f"{temp_dir}/{radom_prefix}-{i}.mp3")
        if audio_clip.duration >= time_per_noun:
            speech_len = audio_clip.duration
        else:
            speech_len = time_per_noun
            silence_audio = AudioClip(make_frame = lambda t: 0, duration = time_per_noun - audio_clip.duration)
            audio_clip = concatenate_audioclips([audio_clip, silence_audio])
        speechs_len.append(speech_len)
        speechs.append(audio_clip)
        os.remove(f"{temp_dir}/{radom_prefix}-{i}.mp3")
    return concatenate_audioclips(speechs), speechs_len

In [9]:
# Below is a set of custom animation functions that will be used in the main function.

def make_ease_in_out_circle_gaussian_global(image_width, image_height, time_per_noun, resume_from=None):
    def ease_in_out_circle_gaussian_global(t):
        surface = gizeh.Surface(image_width, image_height)
        # Calculate radius using a non-linear function (ease-in-out)
        max_radius = np.hypot(image_width, image_height) / 2  # Diagonal of the image
        radius = max_radius * (1 - np.cos(np.pi * t / time_per_noun)) / 2  # Ease-in-out curve
        circle = gizeh.circle(radius, xy=(image_width // 2, image_height // 2), fill=(1, 1, 1))
        circle.draw(surface)
        mask_array = surface.get_npimage()[:, :, 0]
        mask_array = mask_array.astype(np.float32) / 255.0
        height, width = mask_array.shape[:2]
        reduced_mask = cv2.resize(mask_array, (width // 2, height // 2), interpolation=cv2.INTER_AREA)
        blurred_reduced_mask = cv2.GaussianBlur(reduced_mask, (0, 0), sigmaX=7)
        blurred_mask = cv2.resize(blurred_reduced_mask, (width, height), interpolation=cv2.INTER_LINEAR)
        if resume_from is None:
            return blurred_mask
        output_mask = np.clip(blurred_mask + resume_from, 0, 1)
        return output_mask
    return ease_in_out_circle_gaussian_global


# Move to multibbox
def make_ease_in_out_circle_gaussian_bbox(image_width, image_height, bbox, time_per_noun, resume_from=None):
    def ease_in_out_circle_gaussian_bbox(t):
        bbox_width = bbox[2] - bbox[0]
        bbox_height = bbox[3] - bbox[1]
        bbox_center_x = (bbox[0] + bbox[2]) // 2
        bbox_center_y = (bbox[1] + bbox[3]) // 2
        surface = gizeh.Surface(image_width, image_height)
        # Calculate radius using a non-linear function (ease-in-out)
        max_radius = np.hypot(bbox_width, bbox_height) / 2  # Diagonal of the image
        radius = max_radius * (1 - np.cos(np.pi * t / time_per_noun)) / 2  # Ease-in-out curve
        circle = gizeh.circle(radius, xy=(bbox_center_x, bbox_center_y), fill=(1, 1, 1))
        circle.draw(surface)
        mask_array = surface.get_npimage()[:, :, 0]
        mask_array = mask_array.astype(np.float32) / 255.0
        height, width = mask_array.shape[:2]
        reduced_mask = cv2.resize(mask_array, (width // 2, height // 2), interpolation=cv2.INTER_AREA)
        blurred_reduced_mask = cv2.GaussianBlur(reduced_mask, (0, 0), sigmaX=7)
        blurred_mask = cv2.resize(blurred_reduced_mask, (width, height), interpolation=cv2.INTER_LINEAR)
        if resume_from is None:
            return blurred_mask
        output_mask = np.clip(blurred_mask + resume_from, 0, 1)
        return output_mask
    return ease_in_out_circle_gaussian_bbox

def make_image_brighter_bbox(image, bbox, time_per_noun, brightness_factor=2):
    def image_brighter_bbox(t):
        bbox_width = bbox[2] - bbox[0]
        bbox_height = bbox[3] - bbox[1]
        bbox_center_x = (bbox[0] + bbox[2]) // 2
        bbox_center_y = (bbox[1] + bbox[3]) // 2
        surface = gizeh.Surface(image.width, image.height)
        # Calculate radius using a non-linear function (ease-in-out)
        max_radius = np.hypot(bbox_width, bbox_height) / 2  # Diagonal of the image
        radius = max_radius * (1 - np.cos(np.pi * t / time_per_noun)) / 2  # Ease-in-out curve
        circle = gizeh.circle(radius, xy=(bbox_center_x, bbox_center_y), fill=(1, 1, 1))
        circle.draw(surface)
        mask_array = surface.get_npimage()
        mask_array = mask_array.astype(np.float32) / 255.0
        mask_array[:, :, 0] = gaussian_filter(mask_array[:, :, 0], sigma=20)
        mask_array[:, :, 1] = mask_array[:, :, 2] = mask_array[:, :, 0]
        return np.clip(np.array(image) * (1 + brightness_factor * mask_array * ((time_per_noun - t)/time_per_noun)), 0, 255)
    return image_brighter_bbox

def make_image_color_bbox(image, bbox, time_per_noun, dim=1, resume_from=None):
    def image_color_bbox(t, return_mask=False):
        bbox_width = bbox[2] - bbox[0]
        bbox_height = bbox[3] - bbox[1]
        bbox_center_x = (bbox[0] + bbox[2]) // 2
        bbox_center_y = (bbox[1] + bbox[3]) // 2
        surface = gizeh.Surface(image.width, image.height)
        # Calculate radius using a non-linear function (ease-in-out)
        max_radius = np.hypot(bbox_width, bbox_height) / 2  # Diagonal of the bbox
        radius = max_radius * (1 - np.cos(np.pi * t / time_per_noun)) / 2  # Ease-in-out curve
        circle = gizeh.circle(radius, xy=(bbox_center_x, bbox_center_y), fill=(1, 1, 1))
        circle.draw(surface)
        mask_array = surface.get_npimage()
        mask_array = mask_array.astype(np.float32) / 255.0
        mask_array[:, :, 0] = gaussian_filter(mask_array[:, :, 0], sigma=20)
        mask_array[:, :, 1] = mask_array[:, :, 2] = mask_array[:, :, 0]
        image_greyscale = image.convert('L').convert("RGB")
        if resume_from is not None:
            mask_array = np.clip(mask_array + resume_from, 0, 1)
        if return_mask:
            return mask_array
        return np.clip(np.array(image) * mask_array + np.array(image_greyscale) * (1 - mask_array) * dim, 0, 255)

    return image_color_bbox, image_color_bbox(time_per_noun, return_mask=True)

def make_image_color_global(image, time_per_noun, dim=1, resume_from=None):
    def image_color_global(t, return_mask=False):
        surface = gizeh.Surface(image.width, image.height)
        # Calculate radius using a non-linear function (ease-in-out)
        max_radius = np.hypot(image.width, image.height) / 2  # Diagonal of the image
        radius = max_radius * (1 - np.cos(np.pi * t / time_per_noun)) / 2  # Ease-in-out curve
        circle = gizeh.circle(radius, xy=(image.width // 2, image.height // 2), fill=(1, 1, 1))
        circle.draw(surface)
        mask_array = surface.get_npimage()
        mask_array = mask_array.astype(np.float32) / 255.0
        mask_array[:, :, 0] = gaussian_filter(mask_array[:, :, 0], sigma=20)
        mask_array[:, :, 1] = mask_array[:, :, 2] = mask_array[:, :, 0]
        image_greyscale = image.convert('L').convert("RGB")
        if resume_from is not None:
            mask_array = np.clip(mask_array + resume_from, 0, 1)
        if return_mask:
            return mask_array
        return np.clip(np.array(image) * mask_array + np.array(image_greyscale) * (1 - mask_array) * dim, 0, 255)

    return image_color_global, image_color_global(time_per_noun, return_mask=True)

In [10]:
def animate(image, nouns, subtitles, bboxes_per_noun, speech, speechs_len,
            single_bbox=True, time_per_noun=3,
            font_familty="Nimbus-Roman-No9-L-Medium-Italic", mask_animation=None,
            background_animation=None, with_text=True):
    """
    Create an animated video from the processed image and extracted information.

    Args:
        image (np.ndarray): Input image to animate
        nouns (List[str]): List of nouns to highlight
        subtitles (List[str]): List of subtitles to display
        bboxes_per_noun (Dict[str, List[Tuple[float, float, float, float]]]): Bounding boxes for each noun
        speech (AudioClip): MoviePy AudioClip object containing the concatenated speech
        speechs_len (List[float]): List of speech durations
        single_bbox (bool): Whether to use single bounding box per noun
        time_per_noun (float): Time allocated per noun in the animation
        font_family (str): Font family for subtitles
        mask_animation (Optional[str]): Type of mask animation to apply
        background_animation (Optional[str]): Type of background animation to apply
        temp_dir (str): Directory for temporary files

    Returns:
          VideoClip: MoviePy VideoClip object containing the final animation
    """
    if mask_animation not in [None, "reveal"]:
        raise ValueError(f"Unknown mask_animation: {mask_animation}")

    if background_animation not in [None, "brightness", "color", "color-dim"]:
        raise ValueError(f"Unknown background_animation: {background_animation}")

    if background_animation is None:
        if len(subtitles) > len(bboxes_per_noun):
            total_video_duration = speech.duration
        else:
            total_video_duration = speech.duration + time_per_noun
        background = ImageClip(np.array(image)).set_duration(total_video_duration)
    else:
        backgrounds = []

    if with_text:
        fontsize_min = 6
        fontsize_max = 200
        while fontsize_max > fontsize_min:
            fontsize = fontsize_min + (fontsize_max - fontsize_min) // 2
            text = TextClip(subtitles[-1], fontsize=fontsize, color='white', font=font_familty, bg_color="grey10")
            if text.w < image.width * 0.72:
                fontsize_min = fontsize
            elif text.w > image.width * 0.78:
                fontsize_max = fontsize
            else:
                break
        texts = []

    print(f"Fontsize: {fontsize}")
    print(f"Image size: {image.width}, {image.height}")

    masks = []
    prev_mask_final_state = None
    prev_background_mask_final_state = None
    for i, noun in enumerate(nouns):
        bbox = bboxes_per_noun[noun]
        subtitle = subtitles[i]
        speech_len = speechs_len[i]
        # Backgrounds
        if background_animation == "brightness":
            image_brighter_bbox = make_image_brighter_bbox(image, bbox, speech_len)
            background = VideoClip(image_brighter_bbox, duration=speech_len)
            backgrounds.append(background)
        if background_animation == "color":
            image_color_bbox, prev_background_mask_final_state = make_image_color_bbox(image, bbox, speech_len, resume_from=prev_background_mask_final_state)
            background = VideoClip(image_color_bbox, duration=speech_len)
            backgrounds.append(background)
        if background_animation == "color-dim":
            image_color_bbox, prev_background_mask_final_state = make_image_color_bbox(image, bbox, speech_len, dim=0.3, resume_from=prev_background_mask_final_state)
            background = VideoClip(image_color_bbox, duration=speech_len)
            backgrounds.append(background)
        # Masks
        if mask_animation == "reveal":
            ease_in_out_circle_gaussian_bbox = make_ease_in_out_circle_gaussian_bbox(image.width, image.height, bbox, speech_len, resume_from=prev_mask_final_state)
            mask = VideoClip(ease_in_out_circle_gaussian_bbox, duration=speech_len, ismask=True)
            masks.append(mask)
            prev_mask_final_state = ease_in_out_circle_gaussian_bbox(speech_len)
        # Texts
        if with_text:
            # if i == 0:
            #     text = TextClip(subtitle, fontsize=fontsize, color='white', font=font_familty, bg_color="grey10").set_duration(speech_len).fadein(speech_len/2)
            # else:
            text = TextClip(subtitle, fontsize=fontsize, color='white', font=font_familty, bg_color="grey10").set_duration(speech_len)
            texts.append(text)


    if len(subtitles) > len(bboxes_per_noun):
        final_clip_duration = speechs_len[-1]
    else:
        final_clip_duration = time_per_noun
    # Final Background
    if background_animation == "brightness":
        background = ImageClip(np.array(image)).set_duration(final_clip_duration)
        backgrounds.append(background)
        background = concatenate(backgrounds)
    if background_animation == "color":
        image_color_global, _ = make_image_color_global(image, final_clip_duration, resume_from=prev_background_mask_final_state)
        background = VideoClip(image_color_global, duration=final_clip_duration)
        backgrounds.append(background)
        background = concatenate(backgrounds)
    if background_animation == "color-dim":
        image_color_global, _ = make_image_color_global(image, final_clip_duration, dim=0.3, resume_from=prev_background_mask_final_state)
        background = VideoClip(image_color_global, duration=final_clip_duration)
        backgrounds.append(background)
        background = concatenate(backgrounds)
    # Final Mask
    if mask_animation == "reveal":
        ease_in_out_circle_gaussian_global = make_ease_in_out_circle_gaussian_global(image.width, image.height, final_clip_duration, resume_from=prev_mask_final_state)
        mask = VideoClip(ease_in_out_circle_gaussian_global, duration=final_clip_duration, ismask=True)
        masks.append(mask)
    # Final Text
    if with_text:
        text = TextClip(subtitles[-1], fontsize=fontsize, color='white', font=font_familty, bg_color="grey10").set_duration(final_clip_duration)
        texts.append(text)
        text = concatenate(texts).set_position((image.width*0.125, image.height*0.9 - text.h))

    if mask_animation is not None:
        background.mask = concatenate(masks)

    background = background.set_audio(speech)

    if with_text:
        video = CompositeVideoClip([background, text])
    else:
        video = CompositeVideoClip([background])

    video.fps = 24

    return video

In [11]:
def image_to_story(image_location, max_dim=720, time_per_noun=3,
                   tts_library="gtts", elevenlabs_api_key=None,
                   # [UNDER DEVELOPMENT] single_bbox=True, single_bbox_criteria="score",
                   mask_animation=None, background_animation=None,
                   temp_dir="temp"):
    """
    Main function to convert an image into an animated story.

    This function orchestrates the entire process of converting an image into an animated story:
    1. Downloads and processes the input image
    2. Generates a caption and extracts nouns
    3. Detects objects and their bounding boxes
    4. Generates speech from the text
    5. Creates the final animated video

    Args:
        image_location (str): URL or local path to input image
        max_dim (int): Maximum dimension for image resizing
        time_per_noun (float): Time allocated per noun in the animation
        tts_library (str): TTS library to use to generate speech ('gtts' or 'elevenlabs')
        elevenlabs_api_key (str): ElevenLabs API key if using elevenlabs TTS
        # [UNDER DEVELOPMENT] single_bbox (bool): Whether to use single bounding box per noun
        # [UNDER DEVELOPMENT] single_bbox_criteria (str): Criteria for selecting the best bounding box
        mask_animation (Optional[str]): Type of mask animation to apply (None or "reveal")
        background_animation (Optional[str]): Type of background animation to apply (None, "brightness", "color" or "color-dim")
        temp_dir (str): Directory for temporary files

    Returns:
        VideoClip: MoviePy VideoClip object containing the final animated story
    """
    if os.path.exists(temp_dir):
        print(f"[INFO] Temporary directory '{temp_dir}' already exists and will be used. Files might be overwritten in it.")
    else:
        os.mkdir(temp_dir)
        print(f"[INFO] Temporary directory '{temp_dir}' created.")
    print(f"[INFO] Loading and Preprocessing image: {image_location}")
    image = get_image(image_location, max_dim=max_dim)
    print(f"[INFO] Generating caption via BLIP...")
    caption = get_image_caption(image)
    print(f"[INFO] Generated caption: {caption}")
    print(f"[INFO] Identifying nouns in caption...")
    nouns, subtitles, parts_of_speech = get_nouns(caption)
    print(f"[INFO] Identified nouns: {nouns}")
    print(f"[INFO] Detecting bboxes for each noun...")
    bboxes_per_noun = get_nouns_bboxes(image, nouns, single_bbox=True, single_bbox_criteria="score", conf_thr=0.1)
    # [UNDER DEVELOPMENT] detection_options = f"single_bbox={single_bbox}" + (f" and single_bbox_criteria={single_bbox_criteria}" if single_bbox else "")
    # [UNDER DEVELOPMENT] print(f"[INFO] With {detection_options}, detected bboxes per noun: {bboxes_per_noun}")
    print(f"[INFO] Detected bbox per noun: {bboxes_per_noun}")
    nouns, subtitles, parts_of_speech = filter_and_refine(nouns, subtitles, parts_of_speech, bboxes_per_noun)
    print(f"[INFO] Generating speech...")
    speech, speechs_len = get_speech_from_text(parts_of_speech, time_per_noun, tts_library=tts_library, elevenlabs_api_key=elevenlabs_api_key, temp_dir=temp_dir)
    print(f"[INFO] Bringing image to life...")
    return animate(image, nouns, subtitles, bboxes_per_noun, speech, speechs_len, mask_animation=mask_animation, background_animation=background_animation, single_bbox=True, time_per_noun=time_per_noun)

# Inference

In [12]:
# Define ElevenLabs API key if opting to use this TTS.
# More info: https://elevenlabs.io/docs/quickstart
ELEVENLABS_API_KEY = "sk_7c53ca7a09ed5ff447c5012fe32d180dd003c1346fa2e86c"

In [13]:
video = image_to_story("https://cdn.pixabay.com/photo/2014/11/07/00/00/volleyball-520093_1280.jpg",
                       max_dim=480, time_per_noun=2,
                       mask_animation="reveal", background_animation="brightness",
                       tts_library='elevenlabs', elevenlabs_api_key=ELEVENLABS_API_KEY)

# To save video on disk, comment the first line below and uncomment the second one.
# As 'video' is a generator, only one of these lines can be executed.

video.ipython_display(width=480)
#video.write_videofile("result.mp4")

[INFO] Temporary directory 'temp' created.
[INFO] Loading and Preprocessing image: https://cdn.pixabay.com/photo/2014/11/07/00/00/volleyball-520093_1280.jpg
[INFO] Generating caption via BLIP...
[INFO] Generated caption: there is a woman holding a volleyball ball in a gym
[INFO] Identifying nouns in caption...
[INFO] Identified nouns: ['woman', 'volleyball ball', 'gym']
[INFO] Detecting bboxes for each noun...
[INFO] Detected bbox per noun: defaultdict(<class 'list'>, {'volleyball ball': [201, 93, 285, 196], 'gym': [7, 5, 481, 473], 'woman': [0, 0, 315, 318]})
[INFO] Generating speech...
[INFO] Bringing image to life...
Fontsize: 17
Image size: 480, 318
Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [14]:
video = image_to_story("https://cdn.pixabay.com/photo/2018/09/18/21/08/couple-3687274_1280.jpg",
                       max_dim=720, background_animation="color-dim", time_per_noun=2,
                       tts_library='elevenlabs', elevenlabs_api_key=ELEVENLABS_API_KEY)

# To save video on disk, comment the first line below and uncomment the second one.
# As 'video' is a generator, only one of these lines can be executed.

video.ipython_display(width=720)
#video.write_videofile("result.mp4")

[INFO] Temporary directory 'temp' already exists and will be used. Files might be overwritten in it.
[INFO] Loading and Preprocessing image: https://cdn.pixabay.com/photo/2018/09/18/21/08/couple-3687274_1280.jpg
[INFO] Generating caption via BLIP...
[INFO] Generated caption: there are two people walking a dog down a path
[INFO] Identifying nouns in caption...
[INFO] Identified nouns: ['people', 'dog', 'path']
[INFO] Detecting bboxes for each noun...
[INFO] Detected bbox per noun: defaultdict(<class 'list'>, {'path': [108, 141, 579, 477], 'people': [221, 67, 333, 388], 'dog': [489, 263, 594, 406]})
[INFO] Generating speech...
[INFO] Bringing image to life...
Fontsize: 27
Image size: 720, 480
Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [15]:
video = image_to_story("https://cdn.pixabay.com/photo/2023/11/21/13/29/ai-generated-8403412_1280.jpg",
                       mask_animation="reveal", background_animation="brightness", time_per_noun=1.5,
                       tts_library='elevenlabs', elevenlabs_api_key=ELEVENLABS_API_KEY)

# To save video on disk, comment the first line below and uncomment the second one.
# As 'video' is a generator, only one of these lines can be executed.

video.ipython_display(width=720)
#video.write_videofile("result.mp4")

[INFO] Temporary directory 'temp' already exists and will be used. Files might be overwritten in it.
[INFO] Loading and Preprocessing image: https://cdn.pixabay.com/photo/2023/11/21/13/29/ai-generated-8403412_1280.jpg
[INFO] Generating caption via BLIP...
[INFO] Generated caption: cartoon man sitting at a desk with a computer and stuffed animals
[INFO] Identifying nouns in caption...
[INFO] Identified nouns: ['man', 'desk', 'computer', 'animals']
[INFO] Detecting bboxes for each noun...
[INFO] Detected bbox per noun: defaultdict(<class 'list'>, {'computer': [26, 257, 256, 462], 'man': [199, 51, 517, 679], 'desk': [20, 466, 662, 672], 'animals': [12, 566, 137, 675]})
[INFO] Generating speech...
[INFO] Bringing image to life...
Fontsize: 19
Image size: 720, 720
Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [16]:
# https://cdn.pixabay.com/photo/2020/01/31/07/26/chef-4807317_1280.jpg
video = image_to_story("/content/images/chef.jpg",
                       max_dim=720, background_animation="color-dim", time_per_noun=2,
                       tts_library='elevenlabs', elevenlabs_api_key=ELEVENLABS_API_KEY)

# To save video on disk, comment the first line below and uncomment the second one.
# As 'video' is a generator, only one of these lines can be executed.

video.ipython_display(width=720)
#video.write_videofile("result.mp4")

[INFO] Temporary directory 'temp' already exists and will be used. Files might be overwritten in it.
[INFO] Loading and Preprocessing image: /content/images/chef.jpg
[INFO] Generating caption via BLIP...
[INFO] Generated caption: there is a man cooking in a kitchen with a lot of people
[INFO] Identifying nouns in caption...
[INFO] Identified nouns: ['man', 'kitchen', 'lot', 'people']
[INFO] Detecting bboxes for each noun...
[INFO] Detected bbox per noun: defaultdict(<class 'list'>, {'kitchen': [3, 0, 711, 476], 'people': [37, 266, 95, 305], 'man': [362, 58, 654, 480]})
[INFO] Generating speech...
[INFO] Bringing image to life...
Fontsize: 24
Image size: 720, 478
Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4
